In [18]:
import gradio as gr
import tensorflow as tf
import numpy as np
from PIL import Image

In [19]:
%pip install tensorflow tensorflow-datasets gradio pillow matplotlib

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [20]:
model_path = "pokemon-model_transferlearning.keras"
model = tf.keras.models.load_model(model_path)

In [21]:
# Define the core prediction function
def predict_pokemon(image):
    # Preprocess image
    print(type(image))
    image = Image.fromarray(image.astype('uint8'))  # Convert numpy array to PIL image
    image = image.resize((150, 150)) #resize the image to 28x28 and converts it to gray scale
    image = np.array(image)
    image = np.expand_dims(image, axis=0) # same as image[None, ...]
    
    # Predict
    prediction = model.predict(image)
    
    # Because the output layer was dense(0) without an activation function, we need to apply sigmoid to get the probability
    # we could also change the output layer to dense(1, activation='sigmoid')
    prediction = np.round(float(tf.sigmoid(prediction)), 2)
    p_cat = (1 - prediction)
    p_dog = prediction
    return {'cat': p_cat, 'dog': p_dog}

In [22]:
from PIL import Image
import numpy as np
import tensorflow as tf

# Define the core prediction function
def predict_pokemon(image):
    # Preprocess image
    image = Image.fromarray(image.astype('uint8'))  # Convert numpy array to PIL image
    image = image.resize((150, 150)) # Resize the image to 150x150
    image = np.array(image)
    image = np.expand_dims(image, axis=0) # Add batch dimension
    
    # Predict
    prediction = model.predict(image)
    
    # Apply softmax to get probabilities for each class
    probabilities = tf.nn.softmax(prediction)
    
    # Map probabilities to Pokemon classes
    pokemon_classes = ['Articuno', 'Bulbasaur', 'Charmander']  
    probabilities_dict = {pokemon_class: round(float(probability), 2) for pokemon_class, probability in zip(pokemon_classes, probabilities[0])}
    
    return probabilities_dict


In [23]:
# Create the Gradio interface
input_image = gr.Image()
iface = gr.Interface(
    fn=predict_pokemon,
    inputs=input_image, 
    outputs=gr.Label(),
    examples=["images/cat1.jpeg", "images/cat2.jpeg", "images/cat3.jpeg", "images/cat4.jpeg", "images/dog1.jpeg", "images/dog2.jpeg", "images/dog3.jpeg"],   
    description="A simple mlp classification model for image classification using the mnist dataset.")
iface.launch(share=True)

Running on local URL:  http://127.0.0.1:7863
IMPORTANT: You are using gradio version 4.27.0, however version 4.29.0 is available, please upgrade.
--------
Running on public URL: https://a1f42e2a7f46b68a92.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 79ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
